In [2]:
import torch
from torch import nn
import numpy as np
import pandas as pd
import PIL
import glob
import math
import os
import torchvision
import gym
from pyvirtualdisplay import Display
import matplotlib.pyplot as plt
import copy
import time
import random

In [3]:
policy=nn.Sequential(nn.Linear(in_features=2,out_features=32),
                                 nn.ReLU(),
                                 nn.Linear(in_features=32,out_features=64),
                                 nn.ReLU(),
                                 nn.Linear(in_features=64,out_features=128),
                                 nn.ReLU(),
                                 nn.Linear(in_features=128,out_features=256),
                                 nn.ReLU(),
                                 nn.Linear(in_features=256,out_features=128),
                                 nn.ReLU(),
                                 nn.Linear(in_features=128,out_features=1),nn.Tanh())

In [4]:
target_policy=nn.Sequential(nn.Linear(in_features=2,out_features=32),
                                 nn.ReLU(),
                                 nn.Linear(in_features=32,out_features=64),
                                 nn.ReLU(),
                                 nn.Linear(in_features=64,out_features=128),
                                 nn.ReLU(),
                                 nn.Linear(in_features=128,out_features=256),
                                 nn.ReLU(),
                                 nn.Linear(in_features=256,out_features=128),
                                 nn.ReLU(),
                                 nn.Linear(in_features=128,out_features=1),nn.Tanh())

In [5]:
target_value=nn.Sequential(nn.Linear(in_features=3,out_features=32),
                                nn.ReLU(),
                                nn.Linear(in_features=32,out_features=64),
                                nn.ReLU(),
                                nn.Linear(in_features=64,out_features=128),
                                nn.ReLU(),
                                nn.Linear(in_features=128,out_features=256),
                                nn.ReLU(),
                                nn.Linear(in_features=256,out_features=128),
                                nn.ReLU(),
                                nn.Linear(in_features=128,out_features=1))

In [6]:
value=nn.Sequential(nn.Linear(in_features=3,out_features=32),
                                nn.ReLU(),
                                nn.Linear(in_features=32,out_features=64),
                                nn.ReLU(),
                                nn.Linear(in_features=64,out_features=128),
                                nn.ReLU(),
                                nn.Linear(in_features=128,out_features=256),
                                nn.ReLU(),
                                nn.Linear(in_features=256,out_features=128),
                                nn.ReLU(),
                                nn.Linear(in_features=128,out_features=1))

In [7]:
for i in target_policy.parameters():
    i.requires_grad=False
for i in target_value.parameters():
    i.requires_grad=False
for i,j in zip(policy.parameters(),target_policy.parameters()):
    j.data.copy_(i.data)
for i,j in zip(value.parameters(),target_value.parameters()):
    j.data.copy_(i.data)

In [8]:
opt_value=torch.optim.Adam(value.parameters(),lr=0.001)
opt_policy=torch.optim.Adam(policy.parameters(),lr=0.0001)
# learning_rate=0.001

In [12]:
#使用的算法：TD（Q-learning）、Double DQN、Multiple Step、Experience Replay
%matplotlib qt5
buffer_lengthest=50000#replay_buffer总长度为15000
buffer_length_to_train=10000#当replay_buffer的长度达到5000时，开始训练
minibatch_size=100#使用小批量训练，一个批次使用至多60个数据
discount=0.97#折扣回报的折扣率为0.97
env=gym.make('MountainCarContinuous-v0',render_mode='rgb_array')
observation,info=env.reset()
# plt.figure('CartPole-v1',figsize=(4,4))
update_target=0
steps=0
# replay_buffer=[]
while(1):
    small_buffer=[]#创建小buffer，再整体存入replay_buffer中
#     plt.clf()#清除当前图像，必须要有，否则图片会积压住，后来很影响整体代码运行速度
#     plt.imshow(env.render())#显示图像
#     plt.pause(0.00000001)#暂停一小会，如果要用matplotlab显示连续图像，就必须有
    small_buffer.append(list(observation))
#     action=random.uniform(-1,1)
    rand_num=random.randint(0,1)
    if rand_num==0:
        action=random.uniform(0.6,1)
    elif rand_num==1:
        action=random.uniform(-1,-0.6)
    with torch.no_grad():
        action1=policy(torch.from_numpy(observation)).item()
    small_buffer.append(action)
    observation, reward, terminated, truncated, info=env.step([action])#环境执行动作，获得新观测值、奖励以及其他
    #############奖励的设置
    if observation[0]>-0.3 and observation[0]<0.45:
        reward=10*(observation[0]+0.3)**3
    elif observation[0]>=0.45:
        reward=100
    elif observation[0]<=-0.3:
        reward=-0.9
    ####################################
    print('action:',action,'score:',reward,'policy action:',action1)
    small_buffer.append(reward)
    small_buffer.append(list(observation))
    steps+=1
    #下面是开始训练的代码：
    if len(replay_buffer)>=buffer_length_to_train:#当replay_buffer中的数据长度超过buffer_length_to_train的时候才开始训练
        if len(replay_buffer)==buffer_length_to_train:
            print('Start Train')
        how_many=0#在本代码算法结构中，如果在multi_step中遇到自然结束（500步），就舍弃掉这个，how_many就是来计算实际有多少个梯度，用来计算梯度平均
        opt_policy.zero_grad()#将梯度清零
#         for i in policy.parameters():
#             if i.grad is not None:
#                 i.grad.data.zero_()
        opt_value.zero_grad()
        for epoch in range(minibatch_size):#建立循环，minibatch_size个
            drop_this_epoch=0#标识符，用来判断
            end_by_success=0#标识符，用来判断
            target_score=0#TD算法的目标分数，初始化为0
            start_num=random.randint(0,len(replay_buffer)-101)#要在replay_buffer中取样本，用随机数生成第一个数的序号
            len_mult_step=random.randint(2,100)#训练使用multipe_step,也用随机数生成step距离
            for i in range(len_mult_step):
                if replay_buffer[start_num+i][4]==1:#小车成功到达顶点
                    len_mult_step=i+1
                    end_by_success=1#标识符
                    break
                elif replay_buffer[start_num+i][4]==2:#超过999轮，自动停止
                    drop_this_epoch=1#标识符，意味舍弃这一组数据，不计算梯度
                    break
            if drop_this_epoch==1:
                continue#如果遇到自然停止的（超过999），跳出这一轮循环，不计算梯度
            for i in value.parameters():#先将value模型的权重追踪梯度关闭
                i.requires_grad=False
            at_now=policy(torch.tensor(replay_buffer[start_num][0]))
            in_value=torch.cat((torch.tensor(replay_buffer[start_num][0]),at_now),0)
            loss_policy=-value(in_value)#这里原本应该用梯度上升，加个负号用梯度下降
#             loss_policy=value(in_value)
            loss_policy.backward()
            for i in value.parameters():
                i.requires_grad=True
            in_value=torch.cat((torch.tensor(replay_buffer[start_num][0]),torch.tensor([replay_buffer[start_num][1]])),0)
            scoret=value(in_value)#获得t时刻分数
            if end_by_success==1:#如果遇到成功的情况，target_score就是折扣汇报的累加，不需要value计算
                for i in range(len_mult_step):
                    target_score+=replay_buffer[start_num+i][2]*pow(discount,i)
            else:
                for i in range(len_mult_step):
                    target_score+=replay_buffer[start_num+i][2]*pow(discount,i)
                at1=target_policy(torch.tensor(replay_buffer[start_num+len_mult_step-1][3]))
                in_value=torch.cat((torch.tensor(replay_buffer[start_num+len_mult_step-1][3]),at1),0)
                target_score+=target_value(in_value)*pow(discount,len_mult_step)
            loss_value=0.5*pow((scoret-target_score),2)
            loss_value.backward()
            how_many+=1
        for i in value.parameters():#loss.backward会将梯度累加，这里求梯度的平均
            (i.grad.data).div_(how_many)
        for i in policy.parameters():
            (i.grad.data).div_(how_many)
#         for i in policy.parameters():
#             i.data+=i.grad.data*learning_rate
        opt_value.step()#优化器执行
        opt_policy.step()
        update_target+=1
        if update_target>=10:#更新targetDQN
            update_target=0
            for i,j in zip(policy.parameters(),target_policy.parameters()):
                j.data.mul_(0.3)
                j.data.add_((i.data)*0.7)
            for i,j in zip(value.parameters(),target_value.parameters()):
                j.data.mul_(0.3)
                j.data.add_((i.data)*0.7)
    ################################################
    if not (truncated or terminated):
        small_buffer.append(0)
        if len(replay_buffer)>=buffer_lengthest:
            del replay_buffer[0]#如果replay_buffer的总长度大于阈值（3000），则添加新的时候，删掉最老的（序号为0的）
        replay_buffer.append(small_buffer)
    elif terminated:#意味小车成功到达顶点
        small_buffer.append(1)
        if len(replay_buffer)>=buffer_lengthest:
            del replay_buffer[0]
        replay_buffer.append(small_buffer)
        print('The Car Reached Mountaintop Successfully, Episode End, steps=', steps)
        steps=0
        print('The Length of Replay Buffer is ',len(replay_buffer))
        observation,info=env.reset()
    elif truncated:#超过999轮，自动停止
        small_buffer.append(2)
        if len(replay_buffer)>=buffer_lengthest:
            del replay_buffer[0]
        replay_buffer.append(small_buffer)
        print('Episode End by 999')
        steps=0
        observation,info=env.reset()

action: 0.846659287966017 score: -0.9 policy action: 0.9999837279319763
action: 0.6432608432210438 score: -0.9 policy action: 0.9999838471412659
action: 0.8318485816670221 score: -0.9 policy action: 0.999984085559845
action: -0.8379634944090437 score: -0.9 policy action: 0.999984622001648
action: -0.7822146281555243 score: -0.9 policy action: 0.9999845623970032
action: 0.8133287717333698 score: -0.9 policy action: 0.9999842643737793
action: -0.6458202404275897 score: -0.9 policy action: 0.9999844431877136
action: 0.8866274668343188 score: -0.9 policy action: 0.9999841451644897
action: -0.7010778337113666 score: -0.9 policy action: 0.9999842643737793
action: 0.799237280381472 score: -0.9 policy action: 0.9999839067459106
action: 0.7546050242608737 score: -0.9 policy action: 0.9999839663505554
action: 0.6367810607791826 score: -0.9 policy action: 0.9999841451644897
action: 0.7754497562950711 score: -0.9 policy action: 0.9999843835830688
action: 0.8647071592667741 score: -0.9 policy actio

action: -0.6848830267418524 score: -0.9 policy action: 0.9998669028282166
action: -0.8662519793059874 score: -0.9 policy action: 0.999846875667572
action: 0.9188322815161514 score: -0.9 policy action: 0.9998216032981873
action: 0.883130865626222 score: -0.9 policy action: 0.9998000860214233
action: -0.6274295224076638 score: -0.9 policy action: 0.9997809529304504
action: -0.7845770556336653 score: -0.9 policy action: 0.9997572302818298
action: 0.6515738730675095 score: -0.9 policy action: 0.9997298717498779
action: -0.7121645174100197 score: -0.9 policy action: 0.9997093677520752
action: 0.6701702111516942 score: -0.9 policy action: 0.9996843934059143
action: -0.7754773321980308 score: -0.9 policy action: 0.9996695518493652
action: -0.973286693188111 score: -0.9 policy action: 0.9996514320373535
action: 0.8816563113324096 score: -0.9 policy action: 0.999631404876709
action: -0.8346725984559701 score: -0.9 policy action: 0.9996271133422852
action: -0.6340883578874067 score: -0.9 policy 

action: 0.8416759522747265 score: -0.9 policy action: 0.9997358322143555
action: -0.84910143502061 score: -0.9 policy action: 0.9997673630714417
action: -0.9495087989148595 score: -0.9 policy action: 0.9997879862785339
action: 0.6517064946593447 score: -0.9 policy action: 0.9998030066490173
action: 0.8683478984943842 score: -0.9 policy action: 0.9998207092285156
action: -0.8491344204074075 score: -0.9 policy action: 0.9998403787612915
action: 0.6254782860153195 score: -0.9 policy action: 0.9998526573181152
action: -0.8280747218430826 score: -0.9 policy action: 0.9998666644096375
action: 0.9322829266226927 score: -0.9 policy action: 0.9998753666877747
action: -0.7449581687938196 score: -0.9 policy action: 0.9998875856399536
action: -0.6651790693850954 score: -0.9 policy action: 0.9998981952667236
action: 0.9122552001986177 score: -0.9 policy action: 0.9999071955680847
action: -0.7206781373531936 score: -0.9 policy action: 0.9999189376831055
action: -0.8274754019871426 score: -0.9 policy

action: 0.670167563500895 score: -0.9 policy action: 0.244721457362175
action: -0.6049663459977415 score: -0.9 policy action: 0.14825846254825592
action: -0.8199239468155531 score: -0.9 policy action: 0.06427052617073059
action: -0.6978406795930945 score: -0.9 policy action: 0.02822301723062992
action: 0.6583544752066304 score: -0.9 policy action: 0.018666274845600128
action: -0.7133909689071669 score: -0.9 policy action: 0.038503557443618774
action: -0.6148078007585749 score: -0.9 policy action: 0.06197414547204971
action: 0.6156484903206381 score: -0.9 policy action: 0.08449488133192062
action: -0.9054209897346037 score: -0.9 policy action: 0.11087825894355774
action: 0.703294276115364 score: -0.9 policy action: 0.13299982249736786
action: -0.993671514321605 score: -0.9 policy action: 0.17927657067775726
action: -0.8077733980645756 score: -0.9 policy action: 0.2133997678756714
action: 0.6535986177287928 score: -0.9 policy action: 0.23748494684696198
action: 0.87775150204752 score: -0

action: 0.641321558195263 score: -0.9 policy action: -0.15631935000419617
action: 0.9235099060481866 score: -0.9 policy action: -0.05426246300339699
action: 0.8277684952891325 score: -0.9 policy action: 0.10487532615661621
action: 0.7542879869825931 score: -0.9 policy action: 0.2749706506729126
action: 0.63300836874807 score: -0.9 policy action: 0.43625327944755554
action: 0.9630892899942712 score: -0.9 policy action: 0.5854334831237793
action: 0.8631190520400752 score: -0.9 policy action: 0.7114285230636597
action: 0.8780404729937581 score: -0.9 policy action: 0.9002113938331604
action: 0.898547464690552 score: -0.9 policy action: 0.9719913005828857
action: -0.7458343827691296 score: -0.9 policy action: 0.9922659993171692
action: -0.8904046864925763 score: -0.9 policy action: 0.9974272847175598
action: 0.6939494395514074 score: -0.9 policy action: 0.9990248084068298
action: -0.6735826584317655 score: -0.9 policy action: 0.9995689988136292
action: 0.9824320125065026 score: 0.0002094215

...

action: 0.9477647678132082 score: -0.9 policy action: 1.0
action: 0.6660346254883016 score: -0.9 policy action: 1.0
action: -0.9515706366226546 score: -0.9 policy action: 1.0
action: 0.8443652545852607 score: -0.9 policy action: 1.0
action: -0.7846634043845532 score: -0.9 policy action: 1.0
action: 0.641913846077988 score: -0.9 policy action: 1.0
action: -0.6153924127810568 score: -0.9 policy action: 1.0
action: -0.7462137769515806 score: -0.9 policy action: 1.0
action: 0.7692247912484258 score: -0.9 policy action: 1.0
action: 0.6931289995095596 score: -0.9 policy action: 1.0
action: -0.8556143202215581 score: -0.9 policy action: 1.0
action: -0.678222118673955 score: -0.9 policy action: 1.0
action: 0.721444587225371 score: -0.9 policy action: 1.0
action: 0.8067667487330928 score: 3.575778335723073e-05 policy action: 1.0
action: 0.8116160299172047 score: 0.0014973698704654184 policy action: 1.0
action: -0.636269078761069 score: 0.006840904769996951 policy action: 1.0
action: 0.769887599

action: 0.7578502201300531 score: 0.1576395071149636 policy action: 1.0
action: -0.6071473827335236 score: 0.16530071713623457 policy action: 1.0
action: 0.9503955401333704 score: 0.17110325371077145 policy action: 1.0
action: 0.9919139628698287 score: 0.1750261539436562 policy action: 1.0
action: -0.6194627955956076 score: 0.17209720601784287 policy action: 1.0
action: 0.6609895024705391 score: 0.16627432570556713 policy action: 1.0
action: -0.9621816131165413 score: 0.15321327903804394 policy action: 1.0
action: -0.9093711995150433 score: 0.13425205855766062 policy action: 1.0
action: -0.961555240781218 score: 0.11100111039049294 policy action: 1.0
action: 0.8385042998317367 score: 0.08907813976710928 policy action: 1.0
action: -0.6776773476395506 score: 0.06655320195837058 policy action: 1.0
action: 0.9984382102209304 score: 0.047452073864535774 policy action: 0.9999992251396179
action: 0.947731570199069 score: 0.03182945597121992 policy action: -0.9997689723968506
action: 0.8894463

action: -0.8061883476928836 score: -0.9 policy action: 0.7471425533294678
action: -0.7061860802477041 score: -0.9 policy action: -0.9997569918632507
action: -0.7961206409798123 score: -0.9 policy action: -0.9998795986175537
action: -0.9952221712347789 score: -0.9 policy action: -0.9998921155929565
action: 0.6507425320412522 score: -0.9 policy action: -0.9998974800109863
action: -0.6154031049240412 score: -0.9 policy action: -0.9998847842216492
action: -0.9326442460653359 score: -0.9 policy action: -0.9998840689659119
action: 0.6934328416458283 score: -0.9 policy action: -0.9998837113380432
action: -0.9494857532518436 score: -0.9 policy action: -0.9998677372932434
action: 0.7108868271275004 score: -0.9 policy action: -0.9998651146888733
action: 0.823617429566444 score: -0.9 policy action: -0.999845027923584
action: -0.8623647863073155 score: -0.9 policy action: -0.9998120069503784
action: 0.8173540089879492 score: -0.9 policy action: -0.999812662601471
action: 0.8943885739932278 score: 

action: -0.6874527288701423 score: -0.9 policy action: 1.0
action: -0.8718878908520871 score: -0.9 policy action: 0.9999522566795349
action: 0.7318973356967599 score: -0.9 policy action: -0.9990699887275696
action: -0.7622084698377288 score: -0.9 policy action: -0.9966009855270386
action: 0.6447070688169927 score: -0.9 policy action: -0.9998924136161804
action: 0.9938330818923257 score: -0.9 policy action: -0.9998852610588074
action: -0.6034160261517357 score: -0.9 policy action: -0.9998676180839539
action: 0.7256279637167062 score: -0.9 policy action: -0.9998883605003357
action: 0.8949199441885283 score: -0.9 policy action: -0.9998787641525269
action: 0.7048357212452508 score: -0.9 policy action: -0.9998640418052673
action: -0.7820992972035894 score: -0.9 policy action: -0.9998511075973511
action: -0.6759212477030307 score: -0.9 policy action: -0.9998733401298523
action: -0.6783542986184411 score: -0.9 policy action: -0.9998800754547119
action: 0.8995093983072491 score: -0.9 policy ac

KeyboardInterrupt: 

In [26]:
len(replay_buffer)

22781

In [33]:
for i in replay_buffer:
    if i[2]>500:
        print('yes')

yes


In [23]:
%matplotlib qt5
env=gym.make('MountainCarContinuous-v0',render_mode='rgb_array')
observation,info=env.reset()
plt.figure('CartPole-v1',figsize=(4,4))
steps=0
while(1):
    plt.clf()
    plt.imshow(env.render())
    plt.pause(0.000000001)
    print(observation[0],observation[1])
    with torch.no_grad():
        action=policy(torch.from_numpy(observation)).item()
        print('action:',action)
    observation, reward, terminated, truncated, info=env.step([action])
    steps+=1
    if terminated:
        print('The Car Reached Mountaintop Successfully, Episode End, Steps= ',steps)
        break
    elif truncated:
        print('Episode End by 999')
        break
env.close()

-0.5557284 0.0
action: 1.0
-0.5539878 0.0017405992
action: 1.0
-0.5505196 0.0034682013
action: 1.0
-0.5453497 0.005169888
action: 1.0
-0.5385168 0.006832904
action: 1.0
-0.5300721 0.008444753
action: 1.0
-0.5200788 0.009993299
action: 1.0
-0.50861186 0.0114669
action: 1.0
-0.4957573 0.012854536
action: 1.0
-0.48161134 0.014145968
action: 1.0
-0.46627945 0.015331894
action: 1.0
-0.44987532 0.016404115
action: 1.0
-0.43251964 0.017355686
action: 1.0
-0.4143386 0.018181061
action: 1.0
-0.3954624 0.018876204
action: 1.0
-0.3760237 0.019438675
action: 1.0
-0.35615605 0.019867666
action: 1.0
-0.33599207 0.020163998
action: 1.0
-0.315662 0.020330064
action: 1.0
-0.29529226 0.020369735
action: 1.0
-0.27500406 0.020288208
action: 1.0
-0.25491223 0.02009184
action: 1.0
-0.2351243 0.019787928
action: 1.0
-0.2157398 0.019384503
action: 1.0
-0.1968497 0.018890094
action: 1.0
-0.17853619 0.018313507
action: 1.0
-0.16087258 0.017663611
action: 1.0
-0.14392343 0.016949153
action: 1.0
-0.12774484 0.016

In [17]:
torch.save(policy.state_dict(),'./DPG_Policy_MountainCarContinuous_state_dict.pth')

In [18]:
torch.save(value.state_dict(),'./DPG_Value_MountainCarContinuous_state_dict.pth')

In [19]:
torch.save(policy,'./DPG_Policy_MountainCarContinuous_full.pth')

In [20]:
torch.save(value,'./DPG_Value_MountainCarContinuous_full.pth')